In [11]:
from astropy.io.votable import writeto, is_votable, parse
from astropy.table import Table
import numpy as np
import numpy.lib.recfunctions as rec
from sys import exit

# Writes the content of a structured array to a .vot file
def write_array_to_vot(array, outputFile):
    ###################################################
    # IN:                                             #
    #     array      : content to write into the file #
    #     outputFile : file whereto write             #
    ###################################################
    
    #Creates an astropy table and writes it into a file
    table = Table(data=arr)
    writeto(table, outputFile)
    return


# Check whether there are issues with the masking routine
def checking_routine(array, maskNumber):
    ####################################################################################
    # IN:                                                                              #
    #     array      : array on which we check whether the masks worked                #
    #     maskNumber : a flag. If 1 it only tests if the galaxies are out of clusters. # 
    #                          If 2 it tests the CONFID parameter as well.             #
    #                          If 3 it tests the redshift range as well.               #
    ####################################################################################
    
    print("Checking mask number ", maskNumber, ":")
    if  maskNumber>=1:
        if not np.any(array['MUSE_Group_Number'] != -99):
            print("Out of clusters galaxies -> OK")
        else:
            exit("ERROR: At least one galaxy within a cluster")
        if maskNumber>=2:
            if not np.any(array['CONFID']<1):
                print("CONFID -> Ok")
            else:
                exit("ERROR: At least one CONFID<1")
            if maskNumber >=3:
                if np.shape(np.where(np.logical_or(array['Z_MUSE']<0.3, array['Z_MUSE']>1.5)))[1] == 0:
                    print("Redshift -> OK")
                else:
                    exit("ERROR: Redshift <0 or >1.5")
    return

# An improved version of the previous one
def checking_routineV2(array, maskNumber, clusterFlag, confidVal, zMin, zMax):
    #########################################################################################
    # IN:                                                                                   #
    #     array       : array on which we check whether the masks worked                    #
    #     maskNumber  : a flag. If 1 it only tests if the galaxies are out of clusters.     # 
    #                           If 2 it tests the CONFID parameter as well.                 #
    #                           If 3 it tests the redshift range as well.                   #
    #     clusterFlag : flag which indicates if we are looking at cluster or field galaxies #
    #     confidVal   : minmum value of CONFID parameter allowed                            #
    #     zMin        : minimum redshift that we want in the data                           #
    #     zMax        : maximum redshift that we want in the data                           #
    #########################################################################################
    
    #Checking array
    print("Checking mask number ", maskNumber, ":")
    if  maskNumber>=1:
        if not clusterFlag:
            if not np.any(array['MUSE_Group_Number'] != -99):
                print("Out of clusters galaxies -> OK")
            else:
                exit("ERROR: At least one galaxy within a cluster")
        else:
            if not np.any(array['MUSE_Group_Number'] == -99):
                print("Clusters galaxies -> OK")
            else:
                exit("ERROR: At least one galaxy is out of a cluster")
                
        if maskNumber>=2:
            if not np.any(array['CONFID'] < confidVal):
                print("CONFID -> Ok")
            else:
                exit("ERROR: At least one CONFID <", confidVal)
                
            if maskNumber >=3:
                if np.shape(np.where(np.logical_or(array['Z_MUSE'] < zMin, array['Z_MUSE'] > zMax)))[1] == 0:
                    print("Redshift -> OK")
                else:
                    exit("ERROR: Redshift <", zMin, " or >", zMax)
    return

# Move all fields which have type issue between catalogs to the bottom and change their type
def move_bad_fields_to_bottom(oldArray, orderedFieldList, orderedTypeList):
    #################################################################
    # IN:                                                           #
    #      oldArray        : previous array to modify               #
    #      orderFieldList  : list of fields to move and change type #
    #      orderedTypeList : list of new types for the fields       #
    # OUT:                                                          #
    #      outArray        : output array                           #
    #################################################################
    
    outArray = oldArray.copy()
    for name, typ in zip(orderedFieldList, orderedTypeList):
        #Remove field of interest from the array
        tmpArray = rec.rec_drop_fields(outArray, name)
        
        #Append the same field at the end of the array with the right data type
        outArray = rec.rec_append_fields(tmpArray, name, oldArray[name], dtypes=typ)
    return outArray

# Append a new structured array from a catalog to another one
def add_new_array_to_previous(oldArray, fields, fullFileName, firstArray, clusterFlag, confidVal, zMin, zMax):
    ######################################################################
    # IN:                                                                #
    #      oldArray     : previous array whereto append new data         #
    #      fullFileName : location (path+filname) where to retrieve data #
    #      firstArray   : True if first array to build                   #
    # OUT:                                                               #
    #      outArray      : out of clusters + CONFID>1 + z<1.5 galaxies   #            
    ######################################################################
    
    global path, typeList, fieldList
    
    voTag = is_votable(fullFileName)
    print("Is", fullFileName, "a VOtable ? ", voTag)
    if not voTag:
        exit("Given file does not seem to be a VOtable. Exiting code.")
    
    #Only keep fields which are present in every catalog
    table = parse(fullFileName)
    full  = table.get_first_table()
    try:
        array = full.array[fields]
        
    #Dealing with exceptions because of variations in fields names between catalogs
    except ValueError:
        fieldsCopy = np.copy(fields)
        if fullFileName ==  path+"CGR34-32_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot":            
            full.array = rec.rename_fields(full.array, {'groupe_secure_z':'group_secure_z', 
                                           'groupe_unsecure_z':'group_unsecure_z'})
        if fullFileName in (path+"CGR79-77_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot", path+         "CGR32-32-M123_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_withnewz_jan19_withFOF_withGALFIT_withGALKIN_jan19_COSMOSGroupNumberOldCorrected.vot"):
            full.array = rec.rename_fields(full.array, {'TYPE_2':'TYPE', 'secure_z_ss':'secure_z', 
                                      'unsecure_z_ss':'unsecure_z', 'no_z_ss':'no_z', 
                                      'group_secure_z_ss':'group_secure_z', 
                                      'group_unsecure_z_ss':'group_unsecure_z'})
        if fullFileName == path+"CGR32-32-M123_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_withnewz_jan19_withFOF_withGALFIT_withGALKIN_jan19_COSMOSGroupNumberOldCorrected.vot":
            full.array = rec.rename_fields(full.array, {'TYPE_2':'TYPE'})
        if fullFileName == path+"CGR114_116_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot":
            full.array = rec.rename_fields(full.array, {'TYPE_2':'TYPE', 'COSMOS_Group_number':'COSMOS_Group_Number',
                                      'COSMOS_Group_number__old_':'COSMOS_Group_Number__old_',
                                      'FLAG_COSMOS_1':'FLAG_COSMOS'})
        if fullFileName == path+"CGR30-28_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot":
            full.array = rec.rename_fields(full.array, {'TYPE_2':'TYPE', 'ID_Laigle_16_or_ORIGIN':'ID_Laigle_16'})
            
        array = full.array[fields]

    ##################################################
    # Extracting galaxies inside/outside of clusters #
    ##################################################

    if not clusterFlag:
        newArray = array[array['MUSE_Group_Number'] == -99]
    else:
        newArray = array[array['MUSE_Group_Number'] != -99]
    checking_routineV2(newArray, 1, clusterFlag, confidVal, zMin, zMax)

    #################################
    # Extract CONFID=1,2,3 galaxies #
    #################################

    confidArray = newArray[newArray['CONFID'] >= confidVal]
    checking_routineV2(confidArray, 2, clusterFlag, confidVal, zMin, zMax)

    ####################################
    # Extract 0.3<z<1.5 galaxies (OII) #
    ####################################

    finalArray = confidArray[np.logical_and(confidArray['Z_MUSE'] < zMax, confidArray['Z_MUSE'] > zMin)]
    checking_routineV2(finalArray, 3, clusterFlag, confidVal, zMin, zMax)


    #Store fields of interest data type in a list
    for name in fieldList:
        typeList.append(finalArray[name].dtype) 

    #Moving to the bottom  the fields of interest and changing their type
    finalArray = move_bad_fields_to_bottom(finalArray, fieldList, typeList)
       
    if not firstArray:
        #Checking types are equals between fields
        typeOld = oldArray.dtype
        typeNew = finalArray.dtype
        lenOld  = len(typeOld)
        if lenOld != len(typeNew):
            exit("ERROR: old and new arrays do not have the same number of fields. Exiting.")
        listDifference = []
        for i in range(len(typeOld)):
            if typeOld[i] != typeNew[i]:
                listDifference.append(i)
                
        #Print differences in type between fields of old and new arrays if there are some
        for i in listDifference:
            print(oldArray.dtype.names[i], finalArray.dtype.names[i])
            
        outArray = np.append(oldArray, finalArray)
    else:
        outArray = finalArray
    
    return outArray


###MAIN###
path  = "data/catalogues/"
files = ["CGR84-83_FD+North_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_withnewz_jan19_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR34-32_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR79-77_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR32-32-M123_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_withnewz_jan19_withFOF_withGALFIT_withGALKIN_jan19_COSMOSGroupNumberOldCorrected.vot",
         "CGR114_116_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR23-22_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR26-24_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR28-26_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR51-49_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot",
          "CGR61-59_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot",
         "CGR30-28_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot"
        ]

###################
# Free parameters #
###################
clusterFlag = False
confidVal   = 1
zMin        = 0.3
zMax        = 1.5
outName     = "master_field_galaxiesV2.vot"

#Location of fields we want to keep in fields_list file in current folder
fields = np.genfromtxt("fields_list", dtype='str')

#Right data types for fields with incorrect types
fieldList = ['ID', 'COSMOS_Group_Number', 'COSMOS_Group_Number__old_', 
             'PSF_FWHM_o2', 'PSF_FWHM_o3hb']
typeList  = []

#Kepp correct data from each file
arr          = np.array([])
flagArray    = np.full(np.shape(files), False)
flagArray[0] = True

for i, flag in zip(files, flagArray):
     arr = add_new_array_to_previous(arr, fields, path+i, flag, clusterFlag, confidVal, zMin, zMax)
        
#Check everything is correct
print("Fusion completed. Checking one last time.")
checking_routineV2(arr, 3, clusterFlag, confidVal, zMin, zMax)

#Writing result into a file
print("Writing array to file.")
write_array_to_vot(arr, outName)


Is data/catalogues/CGR84-83_FD+North_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_withnewz_jan19_withFOF_withGALFIT_withGALKIN_jan19.vot a VOtable ?  True
Checking mask number  1 :
Out of clusters galaxies -> OK
Checking mask number  2 :
Out of clusters galaxies -> OK
CONFID -> Ok
Checking mask number  3 :
Out of clusters galaxies -> OK
CONFID -> Ok
Redshift -> OK
Is data/catalogues/CGR34-32_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot a VOtable ?  True
Checking mask number  1 :
Out of clusters galaxies -> OK
Checking mask number  2 :
Out of clusters galaxies -> OK
CONFID -> Ok
Checking mask number  3 :
Out of clusters galaxies -> OK
CONFID -> Ok
Redshift -> OK
Is data/catalogues/CGR79-77_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot a VOtable ?  True
Checking mask number  1 :
Out of clusters galaxies -> OK
Checking mask number  2 :
Out of clusters gal

In [12]:
arr['CONFID']

array([3, 3, 3, 2, 2, 1, 2, 2, 3, 3, 1, 1, 1, 3, 3, 2, 3, 1, 1, 2, 3, 3,
       2, 1, 1, 2, 2, 3, 3, 3, 2, 2, 1, 1, 3, 2, 1, 3, 2, 3, 2, 2, 1, 3,
       1, 3, 3, 3, 3, 3, 3, 3, 2, 1, 3, 2, 3, 3, 3, 3, 2, 3, 1, 3, 2, 3,
       3, 3, 3, 3, 2, 2, 3, 3, 3, 3, 3, 2, 1, 2, 2, 2, 2, 2, 2, 2, 2, 3,
       2, 2, 1, 3, 2, 1, 3, 3, 3, 2, 2, 3, 3, 2, 2, 3, 3, 1, 1, 2, 2, 2,
       3, 3, 3, 3, 3, 1, 1, 3, 1, 1, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 1,
       3, 3, 3, 2, 3, 2, 1, 2, 3, 3, 3, 3, 2, 2, 2, 3, 3, 2, 3, 1, 2, 2,
       2, 2, 2, 3, 3, 3, 2, 2, 2, 1, 2, 3, 3, 2, 3, 2, 2, 2, 2, 3, 2, 3,
       1, 2, 3, 1, 2, 3, 1, 2, 1, 1, 2, 2, 2, 3, 2, 2, 2, 2, 2, 1, 2, 2,
       2, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 2, 3, 2, 1, 2, 3, 3, 3, 2, 2,
       3, 3, 2, 2, 3, 3, 1, 1, 2, 3, 2, 3, 3, 3, 3, 3, 2, 2, 2, 2, 2, 1,
       1, 1, 1, 1, 2, 3, 2, 2, 3, 3, 3, 3, 2, 2, 3, 2, 3, 2, 3, 2, 1, 2,
       3, 2, 2, 3, 3, 2, 3, 2, 1, 3, 2, 3, 2, 2, 3, 1, 3, 2, 2, 3, 3, 1,
       3, 2, 3, 3, 3, 3, 1, 3, 1, 2, 2, 2, 2, 3, 3,

In [13]:
arr.shape

(545,)

In [5]:
arr

array([(864084, 150.05237 , 2.607816 , 0.40678, 3, 0, 0, 0, 150.05236955, 2.60781617,               864084, 24248.79101562, 31605.4375    , 2.09458317e-05, 2.07988570e-05, -9.89232390e-06,      0,   5.891214  , 3.5      , 0.01859,      0,      1,      0,      0,  4.81285439e+01,  8.63629505e-02,  6.76302109e+01,  1.4689258e-01,  19.693993,  1.93797657e-03,  19.324648,  2.34575616e-03, 19.083443, 1.45653461e-03, 19.08543 , 1.55183475e-03,      3,      0,  2.29667435e+01,  4.3637358e-02,  3.29145927e+01,  7.35731274e-02,  20.497252,  2.05202587e-03,  20.10653 ,  2.41409591e-03, 19.818157, 1.17460627e-03, 19.833988, 1.26731454e-03,      3,      0,  3.84541359e+01,  9.16221589e-02,  5.42493172e+01,  1.6577618e-01,  19.937643,  2.57324567e-03,  19.564014,  3.30028636e-03, 19.309952, 1.81161647e-03, 19.31924 , 1.94372993e-03,      3,      0,  2.97725067e+01,  6.54302239e-02,  4.22058144e+01,  1.07213758e-01,  20.215462,  2.37348652e-03,  19.836569,  2.74348143e-03, 19.569757, 1.50795537e-03,

In [14]:
from astropy.table import Table
table = Table(data=arr)
table

<Table length=545>
ID_Laigle_16     RA       DEC    ... PSF_FWHM_o2 PSF_FWHM_o3hb
   int32      float64   float64  ...   float64      float64   
------------ ---------- -------- ... ----------- -------------
      864084  150.05237 2.607816 ...      -999.0        -999.0
      868702 150.061897 2.619354 ...      -999.0        -999.0
      866970  150.06035 2.615728 ...      -999.0        -999.0
      862383 150.064951 2.608001 ...      -999.0        -999.0
      868478 150.063779 2.619284 ...      -999.0        -999.0
      868101 150.062285 2.618755 ...      -999.0        -999.0
      859231 150.053047 2.604346 ...      -999.0        -999.0
        9999  150.06765 2.618328 ...      -999.0        -999.0
      868646 150.065015 2.615987 ...      -999.0        -999.0
      866265 150.061336 2.614526 ...      -999.0        -999.0
         ...        ...      ... ...         ...           ...
        9999 150.148048  2.05964 ...      -999.0        -999.0
        9999 150.141694 2.070559 ...      -999.0        -999.0
        9999 150.143675 2.070382 ...      -999.0        -999.0
        9999 150.138701 2.066922 ...      -999.0        -999.0
        9999  150.13659   2.0707 ...      -999.0        -999.0
        9999  150.14683   2.0626 ...      -999.0        -999.0
        9999  150.14893   2.0612 ...      -999.0        -999.0
           2 150.134749 2.068688 ...      -999.0        -999.0
         135 150.144206 2.070633 ...      -999.0        -999.0
         139 150.148153 2.063633 ...      -999.0        -999.0

In [65]:
#         if fullFileName ==  path+"CGR34-32_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot":            
#             fieldsCopy[np.where(fieldsCopy == 'group_secure_z')]            = 'groupe_secure_z'
#             fieldsCopy[np.where(fieldsCopy == 'group_unsecure_z')]          = 'groupe_unsecure_z'
#         if fullFileName in (path+"CGR79-77_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot", path+"CGR32-32-M123_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_withnewz_jan19_withFOF_withGALFIT_withGALKIN_jan19.vot"):
#             fieldsCopy[np.where(fieldsCopy == 'TYPE')]                      = 'TYPE_2'
#             #Check which one between secure_z_ss and secure_z_fd is the right one to use
#             fieldsCopy[np.where(fieldsCopy == 'secure_z')]                  = 'secure_z_ss'
#             fieldsCopy[np.where(fieldsCopy == 'unsecure_z')]                = 'unsecure_z_ss'
#             fieldsCopy[np.where(fieldsCopy == 'no_z')]                      = 'no_z_ss'
#             fieldsCopy[np.where(fieldsCopy == 'group_secure_z')]            = 'group_secure_z_ss'
#             fieldsCopy[np.where(fieldsCopy == 'group_unsecure_z')]          = 'group_unsecure_z_ss'
#         if fullFileName == path+"CGR32-32-M123_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_withnewz_jan19_withFOF_withGALFIT_withGALKIN_jan19.vot":
#             fieldsCopy[np.where(fieldsCopy == 'TYPE')]                      = 'TYPE_2'
#         if fullFileName == path+"CGR114_116_zcatalog_withLaigle+16_withFAST_withPLATEFIT_weightedflux_oct18_withFOF_withGALFIT_withGALKIN_jan19.vot":
#             fieldsCopy[np.where(fieldsCopy == 'COSMOS_Group_Number')]       = 'COSMOS_Group_number'
#             fieldsCopy[np.where(fieldsCopy == 'COSMOS_Group_Number__old_')] = 'COSMOS_Group_number__old_'            
#             fieldsCopy[np.where(fieldsCopy == 'FLAG_COSMOS')]               = 'FLAG_COSMOS_1'
#             fieldsCopy[np.where(fieldsCopy == 'TYPE')]                      = 'TYPE_2'
#         if fullFileName == path+"CGR30-28_FD_zcatalog_withLaigle+16_withFAST_withnewPLATEFIT_totalflux_nov18_withFOF_withGALFIT_withGALKIN_jan19.vot":
#             fieldsCopy[np.where(fieldsCopy == 'ID_Laigle_16')]              = 'ID_Laigle_16_or_ORIGIN'
#             fieldsCopy[np.where(fieldsCopy == 'TYPE')]                      = 'TYPE_2'